In [1]:
import os
import sys
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', 50)

from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

import plotly
import plotly.graph_objs as go
import cufflinks as cf
cf.set_config_file(offline=True)

In [2]:
base_path = os.path.abspath('../..')
data_path = os.path.join(base_path, 'data')
database_path = os.path.join(data_path, 'database')
strategy_path = os.path.join(base_path, 'strategy')
check_path = os.path.join(strategy_path, 'check')
sys.path.append(strategy_path)

In [3]:
from strategy import CommodityStrategy, EquityStrategy, IRStrategy, EmergingStrategy
from tester import Tester

In [4]:
from ICA import ICA
from ICA2 import ICA2
from IEQ import IEQ
from IPM import IPM
from IRV import IRV
from ISS import ISS

# 1. ICA

In [5]:
ica = ICA(strategy_name="ICA", asset_type="IR")
ica.load_index_and_return(from_db=True, save_file=True)
ica.load_strategy_data(table='bloom', origin1='bonds2yr', origin2='bonds10yr')

ica.set_rebalance_period(cs_freq='month', ts_freq='month')
ica.calculate_signal(CS=0.5, nopos=0.4, minobs1=12, use_JGB=False)
ica.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ica.make_portfolio()

2020-02-04 08:56:51,361 - ICA - INFO - [STEP 0] START LOGGING ICA
2020-02-04 08:56:51,364 - ICA - INFO - [STEP 1] LOAD DATA
2020-02-04 08:56:51,365 - ICA - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 08:56:51,374 - ICA - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 08:56:54,559 - ICA - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 08:56:54,602 - ICA - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 08:57:02,209 - ICA - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA.py:55: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA.py:75: FutureWarning:


Passing li

In [6]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ica_comp_df = pd.read_csv('./past/ica.csv', header=0, index_col=0, parse_dates=True)
ica_lag_comp_df = pd.read_csv('./past/ica_lag.csv', header=0, index_col=0, parse_dates=True)

In [7]:
tester = Tester(ica)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 08:57:17,830 - ICA - INFO - [STEP 6] START BACKTEST
2020-02-04 08:57:17,830 - ICA - INFO - [STEP 6 - 1] BACKTEST ICA TIME SERIES


ICA
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 08:57:21,038 - ICA - INFO - [STEP 6 - 2] BACKTEST ICA CROSS SECTIONAL


ICA
0% [############################# ] 100% | ETA: 00:00:00

In [8]:
to_plot = (1.+ ica_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 2. ICA2

In [17]:
ica2 = ICA2(strategy_name="ICA2", asset_type="IR")
ica2.load_index_and_return(from_db=True, save_file=True)
ica2.load_strategy_data(table='bloom', origin1='bonds2yr', origin2='bonds10yr')
ica2.set_rebalance_period(ts_freq='month', cs_freq='month')
ica2.calculate_signal(CS=0.5, minobs=12, use_JGB=False)
ica2.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ica2.make_portfolio()

2020-02-04 09:04:54,220 - ICA2 - INFO - [STEP 0] START LOGGING ICA2
2020-02-04 09:04:54,220 - ICA2 - INFO - [STEP 0] START LOGGING ICA2
2020-02-04 09:04:54,221 - ICA2 - INFO - [STEP 1] LOAD DATA
2020-02-04 09:04:54,221 - ICA2 - INFO - [STEP 1] LOAD DATA
2020-02-04 09:04:54,222 - ICA2 - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:04:54,222 - ICA2 - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:04:54,223 - ICA2 - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:04:54,223 - ICA2 - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:04:58,480 - ICA2 - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:04:58,480 - ICA2 - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:04:58,514 - ICA2 - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:04:58,514 - ICA2 - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:05:06,549 - ICA2 - INFO - [STEP 2] SET REBALANCE PERIO

In [18]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ica2_comp_df = pd.read_csv('./past/ica2.csv', header=0, index_col=0, parse_dates=True)
ica2_lag_comp_df = pd.read_csv('./past/ica2_lag.csv', header=0, index_col=0, parse_dates=True)

In [19]:
tester = Tester(ica2)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 09:05:22,400 - ICA2 - INFO - [STEP 6] START BACKTEST
2020-02-04 09:05:22,400 - ICA2 - INFO - [STEP 6] START BACKTEST
2020-02-04 09:05:22,401 - ICA2 - INFO - [STEP 6 - 1] BACKTEST ICA2 TIME SERIES
2020-02-04 09:05:22,401 - ICA2 - INFO - [STEP 6 - 1] BACKTEST ICA2 TIME SERIES


ICA2
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 09:05:26,222 - ICA2 - INFO - [STEP 6 - 2] BACKTEST ICA2 CROSS SECTIONAL
2020-02-04 09:05:26,222 - ICA2 - INFO - [STEP 6 - 2] BACKTEST ICA2 CROSS SECTIONAL


ICA2
0% [############################# ] 100% | ETA: 00:00:00

In [20]:
to_plot = (1.+ ica2_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 3. IEQ

In [21]:
equity_strategy = EquityStrategy(strategy_name='helper', asset_type='EQUITY')
equity_strategy.load_index_and_return(from_db=True, save_file=True)
ieq = IEQ(strategy_name="IEQ", asset_type="IR")
ieq.load_index_and_return(from_db=True, save_file=True)
ieq.Eindex = equity_strategy.index
ieq.set_rebalance_period(ts_freq='month', cs_freq='month')
ieq.calculate_signal(CS=0.5, nopos=0.4, use_JGB=False)
ieq.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ieq.make_portfolio()

2020-02-04 09:05:31,289 - helper - INFO - [STEP 0] START LOGGING HELPER
2020-02-04 09:05:31,289 - helper - INFO - [STEP 0] START LOGGING HELPER
2020-02-04 09:05:31,289 - helper - INFO - [STEP 0] START LOGGING HELPER
2020-02-04 09:05:31,289 - helper - INFO - [STEP 0] START LOGGING HELPER
2020-02-04 09:05:31,291 - helper - INFO - [STEP 1] LOAD DATA
2020-02-04 09:05:31,291 - helper - INFO - [STEP 1] LOAD DATA
2020-02-04 09:05:31,291 - helper - INFO - [STEP 1] LOAD DATA
2020-02-04 09:05:31,291 - helper - INFO - [STEP 1] LOAD DATA
2020-02-04 09:05:31,293 - helper - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:05:31,293 - helper - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:05:31,293 - helper - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:05:31,293 - helper - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:05:31,295 - helper - INFO - [STEP 1 - 3 ] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:05:31,295 - helper - INFO - [STEP 1

2020-02-04 09:06:32,967 - IEQ - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-02-04 09:06:32,967 - IEQ - INFO - [STEP 5 - 3] MAKE CS POSITION
2020-02-04 09:06:32,970 - IEQ - INFO - [STEP 5 - 3 - 1] TARGET VOL CONTROL to CS POSITION
2020-02-04 09:06:32,970 - IEQ - INFO - [STEP 5 - 3 - 1] TARGET VOL CONTROL to CS POSITION
2020-02-04 09:06:32,970 - IEQ - INFO - [STEP 5 - 3 - 1] TARGET VOL CONTROL to CS POSITION
2020-02-04 09:06:32,970 - IEQ - INFO - [STEP 5 - 3 - 1] TARGET VOL CONTROL to CS POSITION
2020-02-04 09:06:32,975 - IEQ - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-02-04 09:06:32,975 - IEQ - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-02-04 09:06:32,975 - IEQ - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-02-04 09:06:32,975 - IEQ - INFO - [STEP 5 - 3 - 2] ALIGN CS POSITION WITH REBALANCE DAY
2020-02-04 09:06:36,303 - IEQ - INFO - [STEP 5 - 3 - 3] STRATEGY LEVEL VOL CONTROL to CS POSITION
2020-02-04 09:06:36,303 - IEQ - 

In [22]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ieq_comp_df = pd.read_csv('./past/ieq.csv', header=0, index_col=0, parse_dates=True)
ieq_lag_comp_df = pd.read_csv('./past/ieq_lag.csv', header=0, index_col=0, parse_dates=True)

In [23]:
tester = Tester(ieq)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 09:06:37,601 - IEQ - INFO - [STEP 6] START BACKTEST
2020-02-04 09:06:37,601 - IEQ - INFO - [STEP 6] START BACKTEST
2020-02-04 09:06:37,601 - IEQ - INFO - [STEP 6] START BACKTEST
2020-02-04 09:06:37,601 - IEQ - INFO - [STEP 6] START BACKTEST
2020-02-04 09:06:37,603 - IEQ - INFO - [STEP 6 - 1] BACKTEST IEQ TIME SERIES
2020-02-04 09:06:37,603 - IEQ - INFO - [STEP 6 - 1] BACKTEST IEQ TIME SERIES
2020-02-04 09:06:37,603 - IEQ - INFO - [STEP 6 - 1] BACKTEST IEQ TIME SERIES
2020-02-04 09:06:37,603 - IEQ - INFO - [STEP 6 - 1] BACKTEST IEQ TIME SERIES


IEQ
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 09:06:40,790 - IEQ - INFO - [STEP 6 - 2] BACKTEST IEQ CROSS SECTIONAL
2020-02-04 09:06:40,790 - IEQ - INFO - [STEP 6 - 2] BACKTEST IEQ CROSS SECTIONAL
2020-02-04 09:06:40,790 - IEQ - INFO - [STEP 6 - 2] BACKTEST IEQ CROSS SECTIONAL
2020-02-04 09:06:40,790 - IEQ - INFO - [STEP 6 - 2] BACKTEST IEQ CROSS SECTIONAL


IEQ
0% [############################# ] 100% | ETA: 00:00:00

In [24]:
to_plot = (1.+ ieq_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 4. IPM

In [25]:
ipm = IPM(strategy_name="IPM", asset_type="IR")
ipm.load_index_and_return(from_db=True, save_file=True)
ipm.set_rebalance_period(cs_freq='week', ts_freq='week', rebalance_weekday=1)
ipm.calculate_signal(CS=0.5, nopos=0.4, minobs=260, minobs1=52, longlen=52, shortlen=4)
ipm.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ipm.make_portfolio()

2020-02-04 09:06:46,400 - IPM - INFO - [STEP 0] START LOGGING IPM
2020-02-04 09:06:46,400 - IPM - INFO - [STEP 0] START LOGGING IPM
2020-02-04 09:06:46,401 - IPM - INFO - [STEP 1] LOAD DATA
2020-02-04 09:06:46,401 - IPM - INFO - [STEP 1] LOAD DATA
2020-02-04 09:06:46,402 - IPM - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:06:46,402 - IPM - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:06:46,403 - IPM - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:06:46,403 - IPM - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:06:50,914 - IPM - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:06:50,914 - IPM - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:06:50,952 - IPM - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:06:50,952 - IPM - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:06:51,120 - IPM - INFO - [STEP 2] SET REBALANCE PERIOD
2020-02-04 09

In [26]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ipm_comp_df = pd.read_csv('./past/ipm.csv', header=0, index_col=0, parse_dates=True)
ipm_lag_comp_df = pd.read_csv('./past/ipm_lag.csv', header=0, index_col=0, parse_dates=True)

In [27]:
tester = Tester(ipm)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 09:07:08,864 - IPM - INFO - [STEP 6] START BACKTEST
2020-02-04 09:07:08,864 - IPM - INFO - [STEP 6] START BACKTEST
2020-02-04 09:07:08,865 - IPM - INFO - [STEP 6 - 1] BACKTEST IPM TIME SERIES
2020-02-04 09:07:08,865 - IPM - INFO - [STEP 6 - 1] BACKTEST IPM TIME SERIES


IPM
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 09:07:12,654 - IPM - INFO - [STEP 6 - 2] BACKTEST IPM CROSS SECTIONAL
2020-02-04 09:07:12,654 - IPM - INFO - [STEP 6 - 2] BACKTEST IPM CROSS SECTIONAL


IPM
0% [############################# ] 100% | ETA: 00:00:00

In [28]:
to_plot = (1.+ ipm_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 5. IRV

In [29]:
irv = IRV(strategy_name="IRV", asset_type="IR")
irv.load_index_and_return(from_db=True, save_file=True)
irv.load_strategy_data1(table='ds', origin='ERR')
irv.load_strategy_data2(table='bloom', origin1='bonds10yr', origin2='realyield', origin3='realyield2')
irv.set_rebalance_period(ts_freq='month', cs_freq='month')
irv.calculate_signal(CS=0.5, nopos=0.4, minobs=12, use_JGB=False)
irv.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
irv.make_portfolio()

2020-02-04 09:07:18,057 - IRV - INFO - [STEP 0] START LOGGING IRV
2020-02-04 09:07:18,058 - IRV - INFO - [STEP 1] LOAD DATA
2020-02-04 09:07:18,058 - IRV - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:07:18,059 - IRV - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:07:21,428 - IRV - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:07:21,472 - IRV - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:07:30,695 - IRV - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IRV.py:56: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IRV.py:65: FutureWarning:


Passing li

In [30]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
irv_comp_df = pd.read_csv('./past/irv.csv', header=0, index_col=0, parse_dates=True)
irv_lag_comp_df = pd.read_csv('./past/irv_lag.csv', header=0, index_col=0, parse_dates=True)

In [31]:
tester = Tester(irv)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 09:07:47,670 - IRV - INFO - [STEP 6] START BACKTEST
2020-02-04 09:07:47,671 - IRV - INFO - [STEP 6 - 1] BACKTEST IRV TIME SERIES


IRV
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 09:07:50,745 - IRV - INFO - [STEP 6 - 2] BACKTEST IRV CROSS SECTIONAL


IRV
0% [############################# ] 100% | ETA: 00:00:00

In [32]:
to_plot = (1.+ irv_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 6. ISS

In [33]:
iss = ISS(strategy_name="ISS", asset_type="IR")
iss.load_index_and_return(from_db=True, save_file=True)
# iss.load_index_and_return(from_db=False, save_file=False)
iss.set_rebalance_period(ts_freq='day', cs_freq='month')
iss.calculate_signal(CS=0.5, day1=24, short=0.2, use_JGB=False)
iss.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
iss.make_portfolio()

2020-02-04 09:07:56,083 - ISS - INFO - [STEP 0] START LOGGING ISS
2020-02-04 09:07:56,086 - ISS - INFO - [STEP 1] LOAD DATA
2020-02-04 09:07:56,087 - ISS - INFO - [STEP 1 - 1] CONNECT TO BLOOM DATABASE
2020-02-04 09:07:56,087 - ISS - INFO - [STEP 1 - 2] GET DATA FROM BLOOM DATABASE
2020-02-04 09:07:59,648 - ISS - INFO - [STEP 1 - 3] CHANGE BLOOM DATA INTO STANDARD FORMAT
2020-02-04 09:07:59,684 - ISS - INFO - [STEP 1 - 5] SAVE RETURN DATA INTO CSV FORMAT
2020-02-04 09:07:59,836 - ISS - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ISS.py:74: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

2020-02-04 09:08:01,058 - ISS - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-02-04 09:08:01,059 - ISS - 

In [34]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
iss_comp_df = pd.read_csv('./past/iss.csv', header=0, index_col=0, parse_dates=True)
iss_lag_comp_df = pd.read_csv('./past/iss_lag.csv', header=0, index_col=0, parse_dates=True)

In [35]:
tester = Tester(iss)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-02-04 09:08:13,180 - ISS - INFO - [STEP 6] START BACKTEST
2020-02-04 09:08:13,181 - ISS - INFO - [STEP 6 - 1] BACKTEST ISS TIME SERIES


ISS
0% [############################# ] 100% | ETA: 00:00:00

2020-02-04 09:08:16,975 - ISS - INFO - [STEP 6 - 2] BACKTEST ISS CROSS SECTIONAL


ISS
0% [############################# ] 100% | ETA: 00:00:00

In [36]:
to_plot = (1.+ iss_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()